In [44]:
import numpy.random as rd
import numpy as np
import pandas as pd
class Game:
    def __init__(self,n_players, n_suits=4, n_numbers=13):
        self.n_cards = n_suits * n_numbers
        self.n_players=n_players
        self.n_numbers=n_numbers
        self.n_suits=n_suits
        self.cards_in_field = [n_suits] * n_numbers
        self.pairs_acquired = [0]*n_players
        self.unpaired_opened = set()
        self.paired_opened = set()
        
    def start(self):
        turns = 0
        result={
            "settings":{
                "n_cards":self.n_cards,
                "n_numbers":self.n_numbers,
                "n_players":self.n_players,
                "n_suits":self.n_suits
            },
            "history":[]
        }
        
        while self.n_cards:
            assert sum(self.cards_in_field)==self.n_cards
            turns +=1
            player = (turns-1) % self.n_players
            print(f"Turn {turns}, Player {player}")
            # 確定ペアを取得 
            if self.paired_opened:
                # このゲームでは確定ペアは1ペアより多くはならない
                assert len(self.paired_opened)==1
                print(f"player{player} gets {self.paired_opened} from paired opened cards.")
                # ペア処理
                self.pairs_acquired[player] +=len(self.paired_opened)
                self.n_cards -= 2*len(self.paired_opened)
                for card in self.paired_opened:
                    self.cards_in_field[card] -=2
                    
                self.paired_opened = set()
            # 取り切るかペアが引けなかったらやめる
            while self.n_cards:
                # 残りからランダムに引く
                prob=np.array(self.cards_in_field)/self.n_cards
                first_card=rd.choice(len(self.cards_in_field), p=prob)
                self.cards_in_field[first_card]-=1
                self.n_cards -= 1
                    
                if first_card in self.unpaired_opened:
                    # 既にでたカードとペアにしてもう一度
                    self.unpaired_opened.remove(first_card)
                    print(f"player{player} gets {first_card} from random and unpaired_cards.")
                    
                    # ペア処理
                    self.pairs_acquired[player] += 1
                    self.n_cards -= 1
                    self.cards_in_field[first_card] -=1
                else:
                    # もう一度ランダムに引く
                    prob=np.array(self.cards_in_field)/self.n_cards
                    second_card=rd.choice(len(self.cards_in_field), p=prob)
                    if first_card == second_card:
                        print(f"player{player} gets {first_card} from random.")
                        # ペア処理
                        
                        self.pairs_acquired[player] += 1
                        self.n_cards -= 1
                        self.cards_in_field[first_card] -=1
                    else:
                        # 場を元に戻す
                        self.cards_in_field[first_card]+=1
                        self.n_cards += 1
                        
                        if second_card in self.unpaired_opened:
                            # 確定ペアができた場合
                            self.unpaired_opened.remove(second_card)
                            self.paired_opened.add(second_card)
                            self.unpaired_opened.add(first_card)
                        else:
                            # どちらもunpairedに追加
                            self.unpaired_opened.add(first_card)
                            self.unpaired_opened.add(second_card)
                        break

            print(f"rest cards : {self.n_cards}")
            print(self.unpaired_opened)
            print(self.paired_opened)
            print(self.pairs_acquired)
            print(self.cards_in_field)
            turn_result={"turns":turns,"player":player,"rest":self.n_cards,"pairs":list(self.pairs_acquired)}
            result["history"].append(turn_result)
            
        result["pairs"] = self.pairs_acquired
        result["rank"] = list(pd.Series(self.pairs_acquired).rank(method="min", ascending=False))
        return result

In [46]:
game=Game(n_players=4)
game.start()

Turn 1, Player 0
rest cards : 52
{1, 7}
set()
[0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 2, Player 1
rest cards : 52
{1, 10, 5, 7}
set()
[0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 3, Player 2
rest cards : 52
{1, 4, 5, 7, 10, 11}
set()
[0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 4, Player 3
rest cards : 52
{0, 1, 4, 5, 7, 8, 10, 11}
set()
[0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 5, Player 0
player0 gets 3 from random.
rest cards : 50
{1, 4, 5, 7, 8, 9, 10, 11}
{0}
[1, 0, 0, 0]
[4, 4, 4, 2, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 6, Player 1
player1 gets {0} from paired opened cards.
player1 gets 1 from random and unpaired_cards.
rest cards : 46
{4, 5, 6, 8, 9, 10, 11}
{7}
[1, 2, 0, 0]
[2, 2, 4, 2, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 7, Player 2
player2 gets {7} from paired opened cards.
player2 gets 10 from random and unpaired_cards.
rest cards : 42
{0, 4, 5, 6, 8, 9, 11, 12}
set()
[1, 2, 2, 0]
[2, 2, 4, 2, 4, 4, 4, 2, 4, 4, 2, 4, 4]
Turn

{'history': [{'pairs': [0, 0, 0, 0], 'player': 0, 'rest': 52, 'turns': 1},
  {'pairs': [0, 0, 0, 0], 'player': 1, 'rest': 52, 'turns': 2},
  {'pairs': [0, 0, 0, 0], 'player': 2, 'rest': 52, 'turns': 3},
  {'pairs': [0, 0, 0, 0], 'player': 3, 'rest': 52, 'turns': 4},
  {'pairs': [1, 0, 0, 0], 'player': 0, 'rest': 50, 'turns': 5},
  {'pairs': [1, 2, 0, 0], 'player': 1, 'rest': 46, 'turns': 6},
  {'pairs': [1, 2, 2, 0], 'player': 2, 'rest': 42, 'turns': 7},
  {'pairs': [1, 2, 2, 2], 'player': 3, 'rest': 38, 'turns': 8},
  {'pairs': [2, 2, 2, 2], 'player': 0, 'rest': 36, 'turns': 9},
  {'pairs': [2, 3, 2, 2], 'player': 1, 'rest': 34, 'turns': 10},
  {'pairs': [2, 3, 5, 2], 'player': 2, 'rest': 28, 'turns': 11},
  {'pairs': [2, 3, 5, 2], 'player': 3, 'rest': 28, 'turns': 12},
  {'pairs': [4, 3, 5, 2], 'player': 0, 'rest': 24, 'turns': 13},
  {'pairs': [4, 6, 5, 2], 'player': 1, 'rest': 18, 'turns': 14},
  {'pairs': [4, 6, 7, 2], 'player': 2, 'rest': 14, 'turns': 15},
  {'pairs': [4, 6, 7, 9

In [50]:
n_trials=1000
n_players=21
n_suits=4
n_numbers=13

def simulate(n_trials,n_players, n_suits, n_numbers):
    results=[]
    for i in range(n_trials):
        game=Game(n_players, n_suits, n_numbers)
        result = game.start()
        results.append(result)
    return results

In [51]:
results=simulate(n_trials,n_players, n_suits, n_numbers)

Turn 1, Player 0
rest cards : 52
{10, 7}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 2, Player 1
rest cards : 52
{10, 12}
{7}
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 3, Player 2
player2 gets {7} from paired opened cards.
rest cards : 50
{3, 4, 10, 12}
set()
[0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 2, 4, 4, 4, 4, 4]
Turn 4, Player 3
rest cards : 50
{0, 3, 10, 12}
{4}
[0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 2, 4, 4, 4, 4, 4]
Turn 5, Player 4
player4 gets {4} from paired opened cards.
rest cards : 48
{0, 1, 3, 9, 10, 12}
set()
[0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 2, 4, 4, 2, 4, 4, 4, 4, 4]
Turn 6, Player 5
player5 gets 10 from random and unpaired_cards.
rest cards : 46
{0, 3, 9, 11, 12}
{1}
[0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0

set()
[0, 0, 1, 1, 1, 1, 1, 1, 4, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[2, 2, 2, 2, 0, 0, 2, 4, 4, 4, 4, 2, 2]
Turn 11, Player 10
player10 gets 1 from random and unpaired_cards.
player10 gets 3 from random and unpaired_cards.
rest cards : 26
{0, 2, 7, 8, 9}
{6}
[0, 0, 1, 1, 1, 1, 1, 1, 4, 1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[2, 0, 2, 0, 0, 0, 2, 4, 4, 4, 4, 2, 2]
Turn 12, Player 11
player11 gets {6} from paired opened cards.
player11 gets 2 from random and unpaired_cards.
player11 gets 7 from random and unpaired_cards.
player11 gets 0 from random and unpaired_cards.
player11 gets 9 from random and unpaired_cards.
player11 gets 8 from random and unpaired_cards.
rest cards : 14
{7, 10}
set()
[0, 0, 1, 1, 1, 1, 1, 1, 4, 1, 2, 6, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 4, 2, 2]
Turn 13, Player 12
player12 gets 7 from random and unpaired_cards.
rest cards : 12
{10, 11, 12}
set()
[0, 0, 1, 1, 1, 1, 1, 1, 4, 1, 2, 6, 1, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 4

rest cards : 16
{0, 1, 4, 6, 9, 10, 11}
{8}
[0, 0, 1, 1, 3, 1, 1, 0, 5, 0, 0, 3, 0, 3, 0, 0, 0, 0, 0, 0, 0]
[2, 2, 0, 0, 2, 0, 2, 0, 2, 2, 2, 2, 0]
Turn 15, Player 14
player14 gets {8} from paired opened cards.
player14 gets 10 from random and unpaired_cards.
player14 gets 6 from random and unpaired_cards.
player14 gets 9 from random and unpaired_cards.
player14 gets 1 from random and unpaired_cards.
player14 gets 11 from random and unpaired_cards.
player14 gets 4 from random and unpaired_cards.
player14 gets 0 from random and unpaired_cards.
rest cards : 0
set()
set()
[0, 0, 1, 1, 3, 1, 1, 0, 5, 0, 0, 3, 0, 3, 8, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Turn 1, Player 0
rest cards : 52
{8, 10}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 2, Player 1
player1 gets 8 from random and unpaired_cards.
rest cards : 50
{10, 6, 7}
set()
[0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4

player14 gets 0 from random and unpaired_cards.
rest cards : 18
{6, 8, 9, 10, 11}
set()
[0, 0, 0, 0, 1, 3, 1, 2, 1, 1, 3, 1, 1, 1, 2, 0, 0, 0, 0, 0, 0]
[0, 2, 2, 0, 0, 2, 2, 2, 2, 2, 2, 2, 0]
Turn 16, Player 15
rest cards : 18
{1, 5, 6, 8, 9, 10, 11}
set()
[0, 0, 0, 0, 1, 3, 1, 2, 1, 1, 3, 1, 1, 1, 2, 0, 0, 0, 0, 0, 0]
[0, 2, 2, 0, 0, 2, 2, 2, 2, 2, 2, 2, 0]
Turn 17, Player 16
rest cards : 18
{1, 2, 5, 6, 8, 9, 10}
{11}
[0, 0, 0, 0, 1, 3, 1, 2, 1, 1, 3, 1, 1, 1, 2, 0, 0, 0, 0, 0, 0]
[0, 2, 2, 0, 0, 2, 2, 2, 2, 2, 2, 2, 0]
Turn 18, Player 17
player17 gets {11} from paired opened cards.
player17 gets 1 from random and unpaired_cards.
player17 gets 10 from random and unpaired_cards.
player17 gets 9 from random and unpaired_cards.
rest cards : 10
{5, 6, 7, 8}
{2}
[0, 0, 0, 0, 1, 3, 1, 2, 1, 1, 3, 1, 1, 1, 2, 0, 0, 4, 0, 0, 0]
[0, 0, 2, 0, 0, 2, 2, 2, 2, 0, 0, 0, 0]
Turn 19, Player 18
player18 gets {2} from paired opened cards.
player18 gets 5 from random and unpaired_cards.
player18 gets 7

player10 gets 3 from random and unpaired_cards.
rest cards : 28
{1, 2, 4, 6, 7, 10, 11}
set()
[0, 0, 1, 1, 1, 2, 1, 3, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 4, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 2]
Turn 12, Player 11
rest cards : 28
{1, 2, 3, 4, 6, 7, 10}
{11}
[0, 0, 1, 1, 1, 2, 1, 3, 0, 0, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 4, 2, 2, 2, 2, 2, 2, 2, 2, 2, 4, 2]
Turn 13, Player 12
player12 gets {11} from paired opened cards.
player12 gets 2 from random and unpaired_cards.
rest cards : 24
{1, 3, 4, 5, 6, 7, 9, 10}
set()
[0, 0, 1, 1, 1, 2, 1, 3, 0, 0, 3, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 4, 0, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]
Turn 14, Player 13
player13 gets 5 from random and unpaired_cards.
rest cards : 22
{1, 3, 4, 7, 9, 10, 11}
{6}
[0, 0, 1, 1, 1, 2, 1, 3, 0, 0, 3, 0, 2, 1, 0, 0, 0, 0, 0, 0, 0]
[0, 4, 0, 2, 2, 0, 2, 2, 2, 2, 2, 2, 2]
Turn 15, Player 14
player14 gets {6} from paired opened cards.
rest cards : 20
{1, 3, 4, 7, 10, 11, 12}
{9}
[0, 0, 1, 1, 1, 2, 1, 3, 0, 0, 3, 0, 2, 1, 1, 0,

...

[2, 2, 2, 2, 4, 4, 2, 2, 2, 4, 2, 2, 0]
Turn 14, Player 13
player13 gets {0} from paired opened cards.
rest cards : 28
{1, 2, 3, 4, 7, 11}
{9}
[0, 0, 1, 0, 0, 1, 1, 1, 3, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0]
[0, 2, 2, 2, 4, 4, 2, 2, 2, 4, 2, 2, 0]
Turn 15, Player 14
player14 gets {9} from paired opened cards.
player14 gets 11 from random and unpaired_cards.
rest cards : 24
{1, 3, 4, 5, 7}
{2}
[0, 0, 1, 0, 0, 1, 1, 1, 3, 1, 1, 1, 1, 1, 2, 0, 0, 0, 0, 0, 0]
[0, 2, 2, 2, 4, 4, 2, 2, 2, 2, 2, 0, 0]
Turn 16, Player 15
player15 gets {2} from paired opened cards.
rest cards : 22
{1, 3, 4, 7, 9}
{5}
[0, 0, 1, 0, 0, 1, 1, 1, 3, 1, 1, 1, 1, 1, 2, 1, 0, 0, 0, 0, 0]
[0, 2, 0, 2, 4, 4, 2, 2, 2, 2, 2, 0, 0]
Turn 17, Player 16
player16 gets {5} from paired opened cards.
player16 gets 3 from random and unpaired_cards.
rest cards : 18
{1, 4, 8, 9}
{7}
[0, 0, 1, 0, 0, 1, 1, 1, 3, 1, 1, 1, 1, 1, 2, 1, 2, 0, 0, 0, 0]
[0, 2, 0, 0, 4, 2, 2, 2, 2, 2, 2, 0, 0]
Turn 18, Player 17
player17 gets {7} from paired o

Turn 12, Player 11
player11 gets 12 from random and unpaired_cards.
player11 gets 1 from random and unpaired_cards.
player11 gets 3 from random and unpaired_cards.
player11 gets 2 from random and unpaired_cards.
player11 gets 10 from random and unpaired_cards.
rest cards : 22
{2, 3, 5, 6, 7, 8}
set()
[0, 0, 1, 1, 3, 0, 2, 0, 1, 1, 1, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[2, 0, 2, 2, 2, 2, 4, 2, 2, 2, 2, 0, 0]
Turn 13, Player 12
rest cards : 22
{2, 3, 4, 6, 7, 8}
{5}
[0, 0, 1, 1, 3, 0, 2, 0, 1, 1, 1, 5, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[2, 0, 2, 2, 2, 2, 4, 2, 2, 2, 2, 0, 0]
Turn 14, Player 13
player13 gets {5} from paired opened cards.
player13 gets 4 from random and unpaired_cards.
player13 gets 6 from random and unpaired_cards.
player13 gets 8 from random and unpaired_cards.
player13 gets 7 from random and unpaired_cards.
player13 gets 2 from random and unpaired_cards.
rest cards : 10
{0, 3, 10}
set()
[0, 0, 1, 1, 3, 0, 2, 0, 1, 1, 1, 5, 0, 6, 0, 0, 0, 0, 0, 0, 0]
[2, 0, 0, 2, 0, 0, 2, 0, 0, 2, 2

player13 gets 3 from random and unpaired_cards.
player13 gets 11 from random.
rest cards : 8
{5, 8}
set()
[0, 0, 0, 2, 0, 0, 1, 0, 2, 6, 3, 2, 0, 6, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 4, 0, 0, 2, 2, 0, 0, 0]
Turn 15, Player 14
player14 gets 5 from random and unpaired_cards.
player14 gets 8 from random and unpaired_cards.
player14 gets 9 from random.
player14 gets 5 from random.
rest cards : 0
set()
set()
[0, 0, 0, 2, 0, 0, 1, 0, 2, 6, 3, 2, 0, 6, 4, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Turn 1, Player 0
rest cards : 52
{10, 3}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 2, Player 1
rest cards : 52
{8, 10, 3, 5}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 3, Player 2
rest cards : 52
{3, 5, 8, 9, 10, 12}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 4, Player

rest cards : 12
{5, 6}
{4}
[1, 1, 1, 2, 0, 0, 0, 5, 2, 2, 1, 4, 1, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 2, 0, 2, 2, 2, 0, 0, 2, 2, 0, 0]
Turn 14, Player 13
player13 gets {4} from paired opened cards.
player13 gets 5 from random and unpaired_cards.
player13 gets 2 from random.
player13 gets 6 from random and unpaired_cards.
rest cards : 4
{9, 10}
set()
[1, 1, 1, 2, 0, 0, 0, 5, 2, 2, 1, 4, 1, 4, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 0, 0]
Turn 15, Player 14
player14 gets 9 from random and unpaired_cards.
player14 gets 10 from random and unpaired_cards.
rest cards : 0
set()
set()
[1, 1, 1, 2, 0, 0, 0, 5, 2, 2, 1, 4, 1, 4, 2, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Turn 1, Player 0
rest cards : 52
{9, 3}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 2, Player 1
player1 gets 3 from random and unpaired_cards.
player1 gets 0 from random.
rest cards : 48
{8, 9, 4}
set()
[0, 2, 0, 0, 0, 0, 0, 0, 0,

player14 gets 1 from random and unpaired_cards.
rest cards : 0
set()
set()
[0, 1, 2, 1, 0, 1, 1, 5, 2, 0, 1, 2, 5, 3, 2, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Turn 1, Player 0
rest cards : 52
{0, 12}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 2, Player 1
rest cards : 52
{0, 11, 12, 7}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 3, Player 2
rest cards : 52
{0, 6, 7, 9, 11, 12}
set()
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 4, Player 3
rest cards : 52
{0, 7, 8, 9, 11, 12}
{6}
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
[4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]
Turn 5, Player 4
player4 gets {6} from paired opened cards.
player4 gets 11 from random and unpaired_cards.
rest cards : 48
{0, 7, 8, 9, 10}
{12}
[0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 

In [52]:
[len(result["history"]) for result in results]

[17,
 17,
 15,
 17,
 17,
 16,
 16,
 15,
 16,
 14,
 16,
 15,
 18,
 18,
 17,
 18,
 19,
 16,
 15,
 17,
 18,
 18,
 18,
 18,
 17,
 17,
 17,
 16,
 16,
 17,
 16,
 16,
 18,
 18,
 17,
 20,
 15,
 17,
 17,
 17,
 16,
 18,
 15,
 17,
 18,
 17,
 16,
 17,
 16,
 16,
 17,
 18,
 19,
 16,
 18,
 17,
 17,
 18,
 17,
 16,
 17,
 17,
 14,
 15,
 18,
 16,
 19,
 16,
 19,
 17,
 18,
 14,
 18,
 16,
 18,
 16,
 17,
 14,
 16,
 16,
 19,
 17,
 18,
 19,
 18,
 16,
 16,
 19,
 17,
 18,
 16,
 18,
 16,
 17,
 18,
 18,
 17,
 17,
 17,
 17,
 13,
 16,
 18,
 17,
 17,
 13,
 16,
 16,
 18,
 15,
 17,
 17,
 17,
 17,
 17,
 17,
 16,
 17,
 16,
 15,
 17,
 20,
 17,
 18,
 18,
 16,
 15,
 17,
 14,
 17,
 17,
 16,
 17,
 17,
 18,
 16,
 17,
 19,
 18,
 16,
 17,
 16,
 18,
 19,
 16,
 16,
 18,
 15,
 17,
 16,
 19,
 18,
 16,
 18,
 17,
 16,
 17,
 15,
 16,
 16,
 17,
 15,
 18,
 17,
 17,
 17,
 19,
 17,
 18,
 15,
 19,
 18,
 16,
 17,
 14,
 17,
 17,
 17,
 17,
 18,
 18,
 17,
 15,
 17,
 15,
 18,
 17,
 19,
 17,
 15,
 19,
 15,
 15,
 16,
 16,
 16,
 15,
 14,
 16,
 19,
